This notebook will be used mainly for the Capstone Project for the Applied Data Science course on Coursera.


In [829]:
import pandas as pd
import numpy as np
import math

In [492]:
import requests
from pandas.io.json import json_normalize
import geopandas as gpd
from sklearn.cluster import KMeans
from shapely.geometry import Polygon, LineString, Point
from shapely.ops  import transform

In [12]:
# Matplotlib and associated plotting modules
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
#from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 geopandas=0.4.1 --yes 
import folium # map rendering library

Matplotlib is building the font cache; this may take a moment.


Create a map of Edinburgh, split into its natural neighbourhoods.
https://python-visualization.github.io/folium/quickstart.html This is a link for my use later when I want to colour code the map based on similarity.

In [30]:
url = ("https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson" #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
)
neighbourhoods = gpd.read_file(url)
print(neighbourhoods.head())

   OBJECTID             NATURALCOM  OID_  CNT_NATURA  DUMMY_  SUM_ELECNO  \
0         1  Brunstane/Gilberstoun  1485        1485    1485     1485.30   
1         2           Newcraighall   262         262     262      261.77   
2         3              Magdalene  1479        1479    1479     1478.53   
3         4              Newbridge   327         327     327      326.84   
4         5     Cammo/Strathalmond   874         874     874      873.59   

   Z009_ELEC     Shapearea      Shapelen  \
0       1485  1.147451e+06   4629.409487   
1        262  4.414281e+05   3515.734273   
2       1479  3.119711e+05   2590.027278   
3        327  5.567828e+06  11661.263206   
4        874  2.008664e+06   7150.150690   

                                            geometry  
0  POLYGON ((-3.10276 55.94435, -3.10276 55.94435...  
1  MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...  
2  POLYGON ((-3.10240 55.94088, -3.10245 55.94165...  
3  POLYGON ((-3.41296 55.95159, -3.41414 55.95153...  
4  

In [143]:
url = (
    "https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson" #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
)
natural_neighbourhoods = f"{url}"


m = folium.Map(
    location=[55.9533, -3.1883],
    tiles="cartodbpositron",
    zoom_start=13,
)

shapes = folium.GeoJson(natural_neighbourhoods, name="geojson")

shapes.add_to(m)
    
folium.LayerControl().add_to(m)

m

https://geopandas.readthedocs.io/en/latest/gallery/polygon_plotting_with_folium.html example I used to help with the next cell.

In [535]:
path = "https://opendata.arcgis.com/datasets/4082b44746eb4da8b5935be2d3a00185_27.geojson"
df = gpd.read_file(path)

m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    #without simplifying the representation of each borough, the map might not be displayed
    sim_geo = gpd.GeoSeries(r['geometry'])
    #sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

df = df.to_crs(epsg=2163) #set to a projected crs for centroid calculation accuracy.
df['centroids']=df.centroid.to_crs(epsg=4326)
df['lat'] = df['centroids'].y
df['lon'] = df['centroids'].x
df = df.to_crs(epsg=4326)

for _, r in df.iterrows():
    yo = folium.Marker(location=[r['lat'], r['lon']], popup='name: {}'.format(r['NATURALCOM']))
    yo.add_to(m)
print(df)
m

     OBJECTID                 NATURALCOM  OID_  CNT_NATURA  DUMMY_  \
0           1      Brunstane/Gilberstoun  1485        1485    1485   
1           2               Newcraighall   262         262     262   
2           3                  Magdalene  1479        1479    1479   
3           4                  Newbridge   327         327     327   
4           5         Cammo/Strathalmond   874         874     874   
..        ...                        ...   ...         ...     ...   
149       150    Corstorphine/Craigmount  9799        9799    9799   
150       151               Corstorphine  9799        9799    9799   
151       152      Corstorphine/Clerwood  9799        9799    9799   
152       153  The Christians/Portobello  3535        3535    3535   
153       154      Ferryfield/Inverleith  3228        3228    3228   

     SUM_ELECNO  Z009_ELEC     Shapearea      Shapelen  \
0       1485.30       1485  1.147451e+06   4629.409487   
1        261.77        262  4.414281e+05   

In [519]:
CLIENT_ID = "K0K1215GLOMPN31CWAJTTG2MEXDNRZ2UJ1B1PYU0DXCCI3QZ"
CLIENT_SECRET = "E2ROHURCBVBBDLKJQ0MA4L0LQCSXYXLQJFZWVF0QAN3OJMHD"
VERSION = '20180605'
LIMIT = 100

In [940]:


def getNearbyVenues(names, latitudes, longitudes, area):
    
    venues_list=[]
    for name, lat, lng, area2 in zip(names, latitudes, longitudes, area):
        
        radius = 2*math.sqrt(area2/3) #factor of two to account for weirdly shaped areas. This makes a circle with twice the radius of the circle of the same area as the shape.
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId=4d4b7105d754a06374d81259'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            radius,
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['venues']
        
        # return only relevant information for each nearby venue
        venues_list.append([[name, lat, lng, v['name'], v['location']['lat'], v['location']['lng'], v['categories'][0]['name']] for v in results])
        #print([str(v) + "WHOOP" for v in results])
        
        #for v in range(len(results)):
            #venues_list.append(name, lat, lng, v['name'], v['location']['lat'], v['location']['lng'],  v['categories']['name'])
            

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [1006]:
edinburgh_venues = getNearbyVenues(names=df['NATURALCOM'],
                                   latitudes=df['lat'],
                                   longitudes=df['lon'],
                                   area = df['Shapearea']
                                  )
edinburgh_venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0  kingsminor bistrot       55.945272        -3.096003        Breakfast Spot  
1        Costa Coffee       55.933625        -3.105237           Coffee Shop  
2    Twelve Triangles       55.951435        -3.108798                Bakery  
3                 KFC       55.931841        -3.105651  Fast Food Restaurant  
4         Burger King       55.932062        -3.104912  Fast Food Restaurant

Next I need to clean up the dataframe to take out venues that are not inside the neighbourhood boundaries.

In [1007]:
edinburgh_venues_geo = gpd.GeoDataFrame(edinburgh_venues, geometry = gpd.points_from_xy(edinburgh_venues["Venue Longitude"],edinburgh_venues["Venue Latitude"]))
edinburgh_venues_geo.head()


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                Venue  Venue Latitude  Venue Longitude        Venue Category  \
0  kingsminor bistrot       55.945272        -3.096003        Breakfast Spot   
1        Costa Coffee       55.933625        -3.105237           Coffee Shop   
2    Twelve Triangles       55.951435        -3.108798                Bakery   
3                 KFC       55.931841        -3.105651  Fast Food Restaurant   
4         Burger King       55.932062        -3.104912  Fast Food Restaurant   

                    geometry  
0  POINT (-3.09600 55.94527)  
1  POINT (-3.10524 55.93363)  
2  POINT (-3.10880 55.95143)  
3  POINT (-3.10565 55.93184)  
4  POINT (-3.10491 55.93206)

Define a function to find which neighbourhood the venue is really in.

In [1008]:
def which_neighbourhood(test_point):
    for i in range(154):
        if df["geometry"].contains(test_point)[i] == True:
            return df["NATURALCOM"][i]

Run the function for every row of the data frame and drop any rows where the neighbourhood label is not accurate in terms of the natural neighbourhood boundary.

In [1126]:
print(edinburgh_venues_geo.shape)
for ind in edinburgh_venues_geo.index:
    location = edinburgh_venues_geo['geometry'][ind]
    if edinburgh_venues_geo['Neighbourhood'][ind] != which_neighbourhood(location):
        edinburgh_venues_geo.drop(ind, inplace = True)
edinburgh_venues_geo.reset_index(inplace = True)
edinburgh_venues_geo.drop(["index"], axis=1, inplace = True)
print(edinburgh_venues_geo.shape)
edinburgh_venues_geo.head()

(780, 9)
(780, 9)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue  Venue Latitude  Venue Longitude Venue Category  \
0           Costa Coffee       55.941996        -3.101744    Coffee Shop   
1  eh15 Restaurant & Bar       55.943865        -3.098488          Diner   
2                Options       55.944675        -3.096049     Restaurant   
3            Cuddie Brae       55.934582        -3.094717     Restaurant   
4             Alexandros       55.942157        -3.109470           Café   

                    geometry  Venue count  
0  POINT (-3.10174 55.94200)            1  
1  POINT (-3.09849 55.94386)            1  
2  POINT (-3.09605 55.94467)            1  
3  POINT (-3.09472 55.93458)            1  
4  POINT (-3.10947 55.94216)            1

In [1020]:
#edinburgh_venues_geo.reset_index(inplace = True)
edinburgh_venues_geo.drop(["level_0"], axis=1, inplace = True)
edinburgh_venues_geo.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue  Venue Latitude  Venue Longitude Venue Category  \
0           Costa Coffee       55.941996        -3.101744    Coffee Shop   
1  eh15 Restaurant & Bar       55.943865        -3.098488          Diner   
2                Options       55.944675        -3.096049     Restaurant   
3            Cuddie Brae       55.934582        -3.094717     Restaurant   
4             Alexandros       55.942157        -3.109470           Café   

                    geometry  
0  POINT (-3.10174 55.94200)  
1  POINT (-3.09849 55.94386)  
2  POINT (-3.09605 55.94467)  
3  POINT (-3.09472 55.93458)  
4  POINT (-3.10947 55.94216)

Map all venues that are still being used.

In [1021]:
m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

for _, r in edinburgh_venues_geo.iterrows():
    yo = folium.Marker(location=[r['Venue Latitude'], r['Venue Longitude']], popup='name: {}'.format(r['Venue']))
    yo.add_to(m)
m

Use get_dummies to say which type of venue each venue is.

In [1024]:
edin_onehot = pd.get_dummies(edinburgh_venues_geo['Venue Category'])
#, prefix="", prefix_sep=""
print(edin_onehot)
edin_onehot['Neighbourhood'] = edinburgh_venues_geo['Neighbourhood'] 
#Move the Neighbourhood column to the start.
fixed_columns = [edin_onehot.columns[-1]] + list(edin_onehot.columns[:-1])
edin_onehot = edin_onehot[fixed_columns]
edin_onehot.head(10)


     African Restaurant  American Restaurant  Arcade  Asian Restaurant  \
0                     0                    0       0                 0   
1                     0                    0       0                 0   
2                     0                    0       0                 0   
3                     0                    0       0                 0   
4                     0                    0       0                 0   
..                  ...                  ...     ...               ...   
775                   0                    0       0                 0   
776                   0                    0       0                 0   
777                   0                    0       0                 0   
778                   0                    0       0                 0   
779                   0                    0       0                 0   

     Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  Bar  Beach Bar  \
0                        0        

Neighbourhood  African Restaurant  American Restaurant  Arcade  \
0  Brunstane/Gilberstoun                   0                    0       0   
1  Brunstane/Gilberstoun                   0                    0       0   
2  Brunstane/Gilberstoun                   0                    0       0   
3           Newcraighall                   0                    0       0   
4              Magdalene                   0                    0       0   
5              Magdalene                   0                    0       0   
6              Newbridge                   0                    0       0   
7              Newbridge                   0                    0       0   
8              Newbridge                   0                    0       0   
9              Newbridge                   0                    0       0   

   Asian Restaurant  Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                 0                      0          0           0       0   
1                 0                      0          0           0       0   
2                 0                      0          0           0       0   
3                 0                      0          0           0       0   
4                 0                      0          0           0       0   
5                 0                      0          0           0       0   
6                 0                      0          0           0       0   
7                 0                      0          0           0       0   
8                 0                      0          0           0       1   
9                 0                      0          0           0       0   

   Bar  ...  Snack Place  Spanish Restaurant  Steakhouse  Sushi Restaurant  \
0    0  ...            0                   0           0                 0   
1    0  ...            0                   0           0                 0   
2    0  ...            0                   0           0                 0   
3    0  ...            0                   0           0                 0   
4    0  ...            0                   0           0                 0   
5    0  ...            0                   0           0                 0   
6    0  ...            0                   0           0                 0   
7    0  ...            0                   0           0                 0   
8    0  ...            0                   0           0                 0   
9    0  ...            0                   0           0                 0   

   Taco Place  Tapas Restaurant  Tea Room  Thai Restaurant  \
0           0                 0         0                0   
1           0                 0         0                0   
2           0                 0         0                0   
3           0                 0         0                0   
4           0                 0         0                0   
5           0                 0         0                0   
6           0                 0         0                0   
7           0                 0         0                0   
8           0                 0         0                0   
9           0                 0         0                0   

   Turkish Restaurant  Vietnamese Restaurant  
0                   0                      0  
1                   0                      0  
2                   0                      0  
3                   0                      0  
4                   0                      0  
5                   0                      0  
6                   0                      0  
7                   0                      0  
8                   0                      0  
9                   0                      0  

[10 rows x 88 columns]

Find the proportion of each type of venue.

In [1113]:
summed = edin_onehot.sum().drop(["Neighbourhood"])

print(summed.shape)

list_to_use = ["Neighbourhood"]

for i in range(len(summed)):
    if summed[i]>5:
        list_to_use.append(edin_onehot.columns[i+1])
list_to_use

(87,)


['Neighbourhood',
 'Bakery',
 'Bistro',
 'Breakfast Spot',
 'Burger Joint',
 'Café',
 'Chinese Restaurant',
 'Coffee Shop',
 'Deli / Bodega',
 'Diner',
 'English Restaurant',
 'Fast Food Restaurant',
 'Fish & Chips Shop',
 'Gastropub',
 'Ice Cream Shop',
 'Indian Restaurant',
 'Italian Restaurant',
 'Pizza Place',
 'Pub',
 'Restaurant',
 'Sandwich Place',
 'Turkish Restaurant']

In [1114]:

edin_grouped = edin_onehot.groupby('Neighbourhood').mean().reset_index()
edin_grouped = edin_grouped[list_to_use]
edin_grouped.head()

Neighbourhood    Bakery  Bistro  Breakfast Spot  Burger Joint  \
0              Abbeyhill  0.000000     0.0             0.0           0.0   
1               Baberton  0.000000     0.0             0.0           0.0   
2                Balerno  0.000000     0.0             0.0           0.0   
3  Balgreen/Saughtonhall  0.000000     0.0             0.0           0.0   
4               Bankhead  0.166667     0.0             0.0           0.0   

       Café  Chinese Restaurant  Coffee Shop  Deli / Bodega  Diner  ...  \
0  0.307692            0.307692     0.000000            0.0    0.0  ...   
1  0.000000            0.000000     0.000000            0.0    0.0  ...   
2  0.333333            0.000000     0.000000            0.0    0.0  ...   
3  0.000000            0.000000     0.000000            0.0    0.0  ...   
4  0.083333            0.000000     0.083333            0.0    0.0  ...   

   Fish & Chips Shop  Gastropub  Ice Cream Shop  Indian Restaurant  \
0                0.0   0.000000             0.0           0.000000   
1                1.0   0.000000             0.0           0.000000   
2                0.0   0.000000             0.0           0.333333   
3                0.0   0.000000             1.0           0.000000   
4                0.0   0.083333             0.0           0.000000   

   Italian Restaurant  Pizza Place  Pub  Restaurant  Sandwich Place  \
0                 0.0     0.076923  0.0         0.0             0.0   
1                 0.0     0.000000  0.0         0.0             0.0   
2                 0.0     0.000000  0.0         0.0             0.0   
3                 0.0     0.000000  0.0         0.0             0.0   
4                 0.0     0.000000  0.0         0.0             0.0   

   Turkish Restaurant  
0                 0.0  
1                 0.0  
2                 0.0  
3                 0.0  
4                 0.0  

[5 rows x 22 columns]

In [1115]:
for i in list_to_use:
    edin_grouped

In [1121]:
num_top_venues = 3

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = edin_grouped['Neighbourhood']

for ind in np.arange(edin_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(edin_grouped.iloc[ind, :], num_top_venues)
    
neighbourhoods_venues_sorted.head()


Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0              Abbeyhill                  Café    Chinese Restaurant   
1               Baberton     Fish & Chips Shop    Turkish Restaurant   
2                Balerno  Fast Food Restaurant                  Café   
3  Balgreen/Saughtonhall        Ice Cream Shop    Turkish Restaurant   
4               Bankhead  Fast Food Restaurant                Bakery   

  3rd Most Common Venue  
0  Fast Food Restaurant  
1    English Restaurant  
2     Indian Restaurant  
3    English Restaurant  
4                  Café

Create a density measure 

In [1122]:
edinburgh_venues_geo["Venue count"]=1
edinburgh_venues_count = edinburgh_venues_geo.groupby('Neighbourhood').sum().reset_index()
edinburgh_venues_count = edinburgh_venues_count[["Neighbourhood", "Venue count"]]


edinburgh_venues_count = edinburgh_venues_count.join(df.set_index('NATURALCOM'), on='Neighbourhood')

edinburgh_venues_count["Number density"] = edinburgh_venues_count["Venue count"]*10000/edinburgh_venues_count["Shapearea"]


neighbourhoods_venues_sorted["Number density"] = edinburgh_venues_count["Number density"]
print(neighbourhoods_venues_sorted)

             Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0                Abbeyhill                  Café    Chinese Restaurant   
1                 Baberton     Fish & Chips Shop    Turkish Restaurant   
2                  Balerno  Fast Food Restaurant                  Café   
3    Balgreen/Saughtonhall        Ice Cream Shop    Turkish Restaurant   
4                 Bankhead  Fast Food Restaurant                Bakery   
..                     ...                   ...                   ...   
122              Viewforth                  Café                Bakery   
123               West End           Coffee Shop    Italian Restaurant   
124          Wester Coates            Restaurant    Turkish Restaurant   
125          Wester Hailes                Bakery           Pizza Place   
126             Willowbrae                   Pub    Turkish Restaurant   

    3rd Most Common Venue  Number density  
0    Fast Food Restaurant        0.441375  
1      English Restaura

In [1123]:
# set number of clusters
kclusters = 15

edin_grouped_clustering = edin_grouped.drop(['Neighbourhood'], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(edin_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([ 0,  7,  0, 12,  3,  0,  3,  0,  4,  1], dtype=int32)

In [1124]:
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
edin_merged = df[['NATURALCOM','lat','lon','geometry']]

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
edin_merged = edin_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='NATURALCOM')

print(edin_merged)
edin_merged.head(20) # check the last columns!


#print(edin_merged.shape)
edin_merged.dropna(axis=0, how='any', thresh=None, subset=None, inplace=True)

                    NATURALCOM        lat       lon  \
0        Brunstane/Gilberstoun  55.940545 -3.092460   
1                 Newcraighall  55.934650 -3.088188   
2                    Magdalene  55.942010 -3.108687   
3                    Newbridge  55.939694 -3.421174   
4           Cammo/Strathalmond  55.958395 -3.324203   
..                         ...        ...       ...   
149    Corstorphine/Craigmount  55.948396 -3.299799   
150               Corstorphine  55.942325 -3.282735   
151      Corstorphine/Clerwood  55.950484 -3.280013   
152  The Christians/Portobello  55.945476 -3.106248   
153      Ferryfield/Inverleith  55.970581 -3.224060   

                                              geometry  Cluster Labels  \
0    POLYGON ((-3.10276 55.94435, -3.10276 55.94435...             6.0   
1    MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...            10.0   
2    POLYGON ((-3.10240 55.94088, -3.10245 55.94165...             1.0   
3    POLYGON ((-3.41296 55.95159, -3.41414 

In [1125]:
# create map
map_clusters = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.tab20(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# set colour scheme for neighbourhoods
#colors_array2 = cm.coolwarm(np.linspace(0, 1,120))
#colourscheme = [colors.rgb2hex(i) for i in colors_array2]

# add markers to the map
for lat, lon, poi, cluster, top1, top2, top3, sim_geo, density in zip(edin_merged['lat'], edin_merged['lon'], edin_merged['NATURALCOM'], edin_merged['Cluster Labels'], edin_merged['1st Most Common Venue'],edin_merged['2nd Most Common Venue'],edin_merged['3rd Most Common Venue'],edin_merged['geometry'],edin_merged['Number density']):
    
    geo_j = gpd.GeoSeries(sim_geo).to_json()
    style = {'fillColor': '#fcbbf6','fillOpacity': 0.2, 'color': '#fcbbf6', 'opacity':0.4}
    geo_j = folium.GeoJson(data=geo_j, style_function = lambda x: style)
    folium.Popup(poi).add_to(geo_j)
    geo_j.add_to(map_clusters)
    label = folium.Popup(str(poi) +'-------' + ' Cluster ' + str(cluster) + '-------' + '\n Top venue categories: ' + '\n'+ str(top1) + '\n'+ str(top2) + '\n'+ str(top3), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
#folium.LayerControl().add_to(map_clusters)
        
map_clusters

#geopandas.GeoSeries([shapely_polygon]).to_json()

In [987]:
edin_merged[edin_merged["NATURALCOM"].str.contains("Leith")]

NATURALCOM        lat       lon  \
68   Leith/Easter Rd  55.964204 -3.170005   
112            Leith  55.978887 -3.168427   
113      Leith Links  55.967706 -3.157673   

                                              geometry  Cluster Labels  \
68   POLYGON ((-3.17296 55.96908, -3.17297 55.96908...            10.0   
112  POLYGON ((-3.18168 55.99236, -3.18609 55.99082...             9.0   
113  POLYGON ((-3.16618 55.96763, -3.16591 55.96743...            10.0   

    1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue  \
68     Chinese Restaurant            Bagel Shop  Latin American Restaurant   
112                  Café   American Restaurant         Turkish Restaurant   
113    Chinese Restaurant  Fast Food Restaurant          Indian Restaurant   

     Number density  
68         0.179800  
112        0.016513  
113        0.080666